In [1]:
import trading_gym
from trading_gym.registry.gaia.v9.env import GAIAPredictorsContinuousV9
from trading_gym.registry.gaia.v8.env import GAIAPredictorsContinuousV8
from datetime import datetime
from trading_gym.contracts import Cash
from collections import namedtuple
import json
import tensorflow as tf
import os
import pandas as pd
import ray
print(datetime.now())
print(trading_gym.__name__, trading_gym.__version__)
print(ray.__name__, ray.__version__)

2019-08-24 10:39:41.370855
trading_gym 0.8.1
ray 0.7.2


In [2]:
import gym
import numpy as np
import stable_baselines
from stable_baselines.ddpg.policies import MlpPolicy
from stable_baselines.ddpg.policies import LnMlpPolicy
from stable_baselines.common.vec_env import DummyVecEnv
from stable_baselines.ddpg.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise, AdaptiveParamNoiseSpec
from stable_baselines import DDPG

In [3]:
import stable_baselines
print(stable_baselines.__version__)

2.7.0


In [4]:
env_config = dict()
env_config['folds'] =  {
    'training-set': [datetime.min, datetime(2008, 3, 18)],
    'test-set': [datetime(2008, 3, 19), datetime.max],
}

env_config['cost_of_commissions'] = 0.00005
env_config['cost_of_spread'] = 0.0001
env = GAIAPredictorsContinuousV9(env_config)

In [5]:
# gammas = [0.75,0.82, 0.85, 0.9, 0.95, 0.999]
# lrs = [1e-3,1e-2]

In [6]:
# TO DO 
# observe the affects of pruning the action noise. 
# see what the parameter noise actually does 
# increase the batch size, as this is primarily what affects learning (given that it's an off policy algorithm.)
# see if It's worth/I can implement the type of noise that they talk about on the spinning up...

In [7]:
# first give it a go with two folds. 
env = DummyVecEnv([lambda: env])

# the noise objects for DDPG
# for gamma in gammas:
#     for lr in lrs:
        
gamma = 0.95
actor_lr = 1e-5
critic_lr = 1e-5
n_actions = env.action_space.shape[-1]
param_noise = None
param_noise = AdaptiveParamNoiseSpec(initial_stddev=0.1, desired_action_stddev=0.1)
t_steps = 300000

action_noise = OrnsteinUhlenbeckActionNoise(mean=np.zeros(n_actions), sigma=float(0.5) * np.ones(n_actions))

#  if you use param_noise, need to use LnMlpPolicy instead 
model = DDPG(LnMlpPolicy, env,gamma=gamma,verbose=0, param_noise=param_noise, \
             action_noise=action_noise,actor_lr= actor_lr,critic_lr=critic_lr )
model.learn(total_timesteps=t_steps)
t_steps = '300k'
model.save("saved_models/2folds_tuning/DDPG_comissions/DDPG_v9_steps={}_lr={}_gamma={}_paramnoise".format(t_steps,actor_lr,gamma))

# del model # remove to demonstrate saving and loading

In [8]:
env_config = dict()
env_config['folds'] =  {
    'training-set': [datetime.min, datetime(2008, 3, 18)],
    'test-set': [datetime(2008, 3, 19), datetime.max],
}

env_config['cost_of_commissions'] = 0.00001
env_config['cost_of_spread'] = 0.0001
env = GAIAPredictorsContinuousV9(env_config)
env

env = DummyVecEnv([lambda: env])

obs = env.reset()
for i in range(1000):
        action, _states = model.predict(obs,deterministic=True)
        print(action)
        obs,rewards,dones,info = env.step(action)

[[ 0.09990555 -0.09999968]]
[[-0.00293441 -0.09999201]]
[[-0.06957727 -0.09991264]]
[[-0.02508563 -0.09998551]]
[[-0.00342819  0.09979426]]
[[-0.05280064 -0.09999977]]
[[0.03936936 0.0910984 ]]
[[ 0.07850006 -0.09999983]]
[[ 0.05266253 -0.09999571]]
[[-0.05002989  0.09925634]]
[[-0.03403448 -0.09999848]]
[[ 0.00325651 -0.09999735]]
[[ 0.00197055 -0.09999634]]
[[0.09999198 0.0987622 ]]
[[ 0.05734545 -0.09225021]]
[[ 0.09548101 -0.09999987]]
[[ 0.00477479 -0.09999614]]
[[ 0.0226137  -0.09999695]]
[[ 0.02891465 -0.0999968 ]]
[[-0.0996959  -0.09994366]]
[[-0.09999748  0.05733529]]
[[-0.09999802  0.021866  ]]
[[-0.09999819 -0.02851643]]
[[-0.09999834 -0.03840176]]
[[-0.09999847 -0.03641126]]
[[-0.09999857 -0.03687717]]
[[-0.09999861 -0.03724505]]
[[-0.09999859 -0.03729952]]
[[-0.0999985  -0.03884951]]
[[-0.09999837 -0.04105215]]
[[-0.09999813 -0.04364205]]
[[-0.09999778 -0.04681256]]
[[-0.09999733 -0.05187516]]
[[-0.09999672 -0.05646572]]
[[-0.09999622 -0.05958049]]
[[-0.09999558 -0.0628298

[[-9.80766024e-05  9.89142299e-02]]
[[-0.07840035 -0.09999672]]
[[-0.03616598 -0.09999923]]
[[-0.0411658  -0.09999695]]
[[-0.04285823 -0.09999576]]
[[0.01309573 0.08540823]]
[[0.09474221 0.09982222]]
[[0.09909102 0.09974775]]
[[-0.0535045  -0.09998332]]
[[0.09973521 0.09727941]]
[[ 0.09969872 -0.01212828]]
[[ 0.09937432 -0.07614686]]
[[ 0.08329554 -0.09824088]]
[[ 0.03527739 -0.07038956]]
[[-0.0246542  -0.09941144]]
[[ 0.03869528 -0.09999956]]
[[0.09944059 0.07582899]]
[[-0.0671886  -0.09925336]]
[[0.08736448 0.09559592]]
[[0.0993731  0.09639335]]
[[ 0.09976338 -0.08443495]]
[[ 0.09994506 -0.03176779]]
[[ 0.0302702  -0.08357082]]
[[ 0.03240384 -0.0827441 ]]
[[ 0.09979254 -0.09999977]]
[[-0.06218495 -0.09999831]]
[[-0.03772589 -0.09999929]]
[[-0.0411658  -0.09999695]]
[[-0.04285823 -0.09999576]]
[[0.01309573 0.08540823]]
[[0.09474221 0.09982222]]
[[0.09909102 0.09974775]]
[[-0.0535045  -0.09998332]]
[[0.09973521 0.09727941]]
[[ 0.09969872 -0.01212828]]
[[ 0.09937432 -0.07614686]]
[[ 0.0

[[ 0.06323458 -0.09988045]]
[[ 0.09999424 -0.09278049]]
[[ 0.09998451 -0.09983312]]
[[ 0.09996765 -0.09926571]]
[[ 0.09919773 -0.0893353 ]]
[[ 0.0900566  -0.08965993]]
[[ 0.09955978 -0.09957904]]
[[ 0.05421278 -0.09989725]]
[[0.06422203 0.00181518]]
[[-0.04616097 -0.0971867 ]]
[[-0.06013032 -0.09847663]]
[[ 0.04113238 -0.0059895 ]]
[[0.09894447 0.08506227]]
[[ 0.08706123 -0.09999961]]
[[-0.00775135 -0.09999881]]
[[ 0.08413639 -0.09999982]]
[[-0.09833661 -0.09643127]]
[[-0.02600755 -0.09999169]]
[[-0.09883586 -0.09531705]]
[[-0.09921193 -0.00613754]]
[[-0.00579431  0.09805738]]
[[0.07281048 0.09632058]]
[[ 0.07070971 -0.09999979]]
[[-0.02328167  0.09963021]]
[[-0.09648194 -0.0985306 ]]
[[-0.09815066 -0.09448552]]
[[-0.02472944  0.08895245]]
[[0.09977112 0.07561059]]
[[-0.05878878 -0.09982297]]
[[-0.01939913 -0.0999993 ]]
[[ 0.01679358 -0.09999971]]
[[-0.01577949 -0.09999892]]
[[-0.09597805 -0.09976344]]
[[ 0.0759119  -0.09999966]]
[[ 0.09998999 -0.0157089 ]]
[[-0.03869856 -0.09903407]]


[[ 0.06057557 -0.03909151]]
[[ 0.09774403 -0.03519692]]
[[ 0.09794908 -0.04237084]]
[[ 0.01904763 -0.07462103]]
[[ 0.08826615 -0.04602045]]
[[ 0.09004506 -0.02684408]]
[[0.08177716 0.04564967]]
[[0.02935847 0.09761907]]
[[0.09562911 0.09562613]]
[[0.09994621 0.05806168]]
[[-0.06082091  0.09992457]]
[[ 0.09999949 -0.09561182]]
[[ 0.09975854 -0.0485757 ]]
[[0.09562482 0.07825497]]
[[ 0.09999902 -0.09325418]]
[[ 0.0673143  -0.05206746]]
[[ 0.06598583 -0.01895283]]
[[0.0877473  0.06799669]]
[[0.04015188 0.08318873]]
[[ 0.08398063 -0.06528581]]
[[ 0.02022492 -0.05249079]]
[[0.06770449 0.09341701]]
[[ 0.09617481 -0.02401121]]
[[-0.02154523  0.09175277]]
[[0.09218665 0.02667221]]
[[ 0.09999269 -0.09241027]]
[[ 0.04105719 -0.05598598]]
[[0.08741011 0.0262915 ]]
[[0.05945129 0.00076975]]
[[ 0.09019193 -0.09996582]]
[[ 0.09590157 -0.06246018]]
[[ 0.09701992 -0.09394586]]
[[ 0.08366966 -0.04882485]]
[[ 0.09760323 -0.08547077]]
[[ 0.09555236 -0.01850897]]
[[ 0.09881566 -0.09677615]]
[[ 0.05744303 

In [ ]:
##### t_steps = 50000
t_steps = '300k'
# t_steps = '500k'
# t_steps = '1mill'

# gammas = [0.75,0.82, 0.85, 0.9, 0.95, 0.999]
# lrs = [1e-3,1e-2,1e-4,1e-5]

actor_lr = 1e-5
gamma = 0.95

path = "saved_models/2folds_tuning/DDPG_comissions/DDPG_v9_steps={}_lr={}_gamma={}_paramnoise".format(t_steps,actor_lr,gamma)

model= DDPG.load(path)

# note that the number of steps will be shown in the tensorboard plots 
data,params = DDPG._load_from_file(path)

print("The config is: \n ",data)


In [ ]:
env_config = dict()
env_config['folds'] =  {
    'training-set': [datetime.min, datetime(2008, 3, 18)],
    'test-set': [datetime(2008, 3, 19), datetime.max],
}
env_config['cost_of_commissions'] = 0.00005
env_config['cost_of_spread'] = 0.0001
env = GAIAPredictorsContinuousV9(env_config)
env

In [25]:

episode = env.sample_episode(
        fold = 'test-set',
        stable_model=True,
        model=model,
        episode_length=None,
        benchmark=env._load_benchmark().squeeze(),
        risk_free=env._load_risk_free().squeeze(),
        burn=1,
    )
episode.renderer.plotly_report()
episode.renderer.tearsheet()

Strategy  \
Context              From                                       2008-03-19   
                     To                                         2018-08-28   
                     Years                                         10.4493   
                     Observations                                     2725   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                             0.00681294   
Return               CAGR                                        0.0901938   
                     CAGR over cash                              0.0833808   
                     Overall return                                 1.4654   
Risk                 Volatility                                  0.0842375   
                     Downside volatility                         0.0626777   
                     Upside volatility                           0.0577031   
                     Max drawdown                                -0.115528   
                     Martin risk                                 0.0342589   
                     VaR 5%                                    -0.00842317   
                     VaR 2%                                     -0.0120846   
                     Expected shortfall 5%                      -0.0124746   
                     Expected shortfall 2%                      -0.0162128   
Risk-adjusted return Sharpe ratio                                  0.98983   
                     Sortino ratio                                 1.33031   
                     Calmar ratio                                 0.721737   
                     Martin ratio                                  2.43385   
Outperformance       Benchmark name                  Index(Aric-Benchmark)   
                     CAGR over benchmark                        -0.0683918   
                     Information ratio                           -0.918564   
                     CAPM Alpha                                 -0.0013193   
                     CAPM Beta                                    0.582264   
Weights              Cash(USD)                                  0.00371446   
                     ETF(Russell 1000, SMART, USD)                0.403323   
                     ETF(7-10Y T-Bills, SMART, USD)               0.592963   
                     Leverage mean                                       1   
                     Turnover daily                              0.0639033   
                     Turnover annual                               16.1036   

                                                     Index(Aric-Benchmark)  \
Context              From                                       2008-03-19   
                     To                                         2018-08-28   
                     Years                                         10.4493   
                     Observations                                     2725   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                             0.00681294   
Return               CAGR                                         0.158586   
                     CAGR over cash                               0.151773   
                     Overall return                                3.65592   
Risk                 Volatility                                  0.0970738   
                     Downside volatility                          0.069906   
                     Upside volatility                           0.0705399   
                     Max drawdown                               -0.0865477   
                     Martin risk                                 0.0189993   
                     VaR 5%                                    -0.00895352   
                     VaR 2%                                     -0.0134313   
                     Expected shortfall 5%                      -0.0137858   
         

Interesting to note that the turnover is quite large, therefore it might be wise to reduce the action bound for my algorithm, so that it's not too large (i.e. 0.05 instead of 0.1) 

In [58]:
result = dict()
for fold in env._transmitter.folds.folds.keys():
    episode = env.sample_episode(fold, stable_model=True,model=model)
    env.broker.track_record.burn = 1
    nlv = episode.track_record.to_frame('nlv').iloc[1:]
    weights = episode.track_record.to_frame('weights_target')
    mid_prices = env.exchange.get_historical_prices()
    mid_prices.pop(env.idle_cash_rate)
    mid_prices.pop(Cash())
    mid_prices = pd.DataFrame(mid_prices)
    tearsheet = nlv.tearsheet(
        benchmark=env_config['benchmark'].dropna(),
        risk_free=env_config['risk_free'],
        weights=weights,
        prices=mid_prices,
    )
    result[fold] = {
        'tearsheet': tearsheet,
        'total_reward': np.nansum(episode.rewards),
    }

# 3. Attempt walk-forward training

In [9]:
# gammas = [0.95, 0.999]
# lrs = [1e-3,1e-4,1e-5]

gammas = [0.95]
lrs = [1e-5]

In [10]:
for gamma in gammas: 
    for lr in lrs: 
        

        for year in range(2007, 2018):
            print('_______________________________________{}____________________________________________'.format(year))

            # walk-forward env fold settings

            env_config = dict()

            env_config['folds'] = {
                    'training-set': [datetime.min, datetime(year, 12, 31)],
                    'test-set': [datetime(year + 1, 1, 1), datetime(year + 1, 12, 31)],
                }

#             env_config['cost_of_commissions'] = 0.00005
#             env_config['cost_of_spread'] = 0.0001
            env = GAIAPredictorsContinuousV9(env_config)
            env = DummyVecEnv([lambda: env])

            # the noise objects for DDPG
            actor_lr = lr
            critic_lr = lr
            n_actions = env.action_space.shape[-1]
            param_noise = None
            # param_noise = AdaptiveParamNoiseSpec(initial_stddev=0.1, desired_action_stddev=0.1)
            t_steps = 500000

            action_noise = OrnsteinUhlenbeckActionNoise(mean=np.zeros(n_actions), sigma=float(0.5) * np.ones(n_actions))

            #  if you use param_noise, need to use LnMlpPolicy instead 

            model = DDPG(MlpPolicy, env,gamma=gamma, verbose=0, param_noise=param_noise,\
                         action_noise=action_noise,actor_lr= actor_lr,critic_lr=critic_lr)
            model.learn(total_timesteps=t_steps)

    #         t_steps = '300k'
            model.save("saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr={}_gamma={}_{}".format(lr,gamma,year))

            # to do: 
            # add the tensorboard plots once i've got them working
            # do layer normalisation 
            # do hyperparam optimisation 

_______________________________________2007____________________________________________
_______________________________________2008____________________________________________
_______________________________________2009____________________________________________
_______________________________________2010____________________________________________
_______________________________________2011____________________________________________
_______________________________________2012____________________________________________
_______________________________________2013____________________________________________
_______________________________________2014____________________________________________
_______________________________________2015____________________________________________
_______________________________________2016____________________________________________
_______________________________________2017____________________________________________


Now let us restore this agent

In [12]:
# t_steps = '50k'
# t_steps = '100k'
# t_steps = '500k'
t_steps = '50ksteps'
# t_steps = '300k'
steps ='50k'

lr = 1e-5
gamma = 0.95


paths = {2007: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2007' ,
        2008: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2008',
        2009: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2009',
        2010: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2010',
        2011: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2011',
        2012: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2012',
        2013: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2013',
        2014: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2014',
        2015: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2015',
        2016: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2016',
        2017: '/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG/NEW_EXPS/wf_DDPG_v9_lr=1e-05_gamma=0.95_2017',
        }

# paths = {2007:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2007',
# 2008:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2008',
# 2009:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2009',
# 2010:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2010',
# 2011:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2011',
# 2012:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2012',
# 2013:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2013',
# 2014:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2014',
# 2015:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2015',
# 2016:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2016',
# 2017:'/home/Nicholas/trading-gym/notebooks/trading-gym/walk-forward/saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2017'}


# paths = {2007: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2007',
#         2008: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2008',
#         2009: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2009',
#         2010: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2010',
#         2011: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2011',
#         2012: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2012',
#         2013: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2013',
#         2014: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2014',
#         2015: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2015',
#         2016: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2016',
#         2017: 'saved_models/walk-forward/DDPG_commissions/high_commissions/300ksteps/lr0.001_gamma0.75/wf_DDPG_v9_lr=0.001_gamma=0.75_2017',
#         }

In [18]:
episodes = dict()
agents = dict()
for year, path in paths.items():
    print('_______________________________________{}____________________________________________'.format(year))
    
    model = DDPG.load(path)
    
    env_config = dict()
    env_config['folds'] =  {
        'training-set': [datetime.min, datetime(year, 12, 31)],
        'test-set': [datetime(year + 1, 1, 1), datetime(year + 1, 12, 31)],
    }
    env_config['cost_of_commissions'] = 0.00005
    env_config['cost_of_spread'] = 0.0001
    
    env = GAIAPredictorsContinuousV9(env_config)
    
    episode = env.sample_episode(
        fold = 'test-set',
        stable_model=True,
        model=model,
        episode_length=None,
        benchmark=env._load_benchmark().squeeze(),
        risk_free=env._load_risk_free().squeeze(),
        burn=1,
    )
    episode.renderer.plotly_report()
#     print(episode.renderer.tearsheet())
    

    episodes[year] = episode

_______________________________________2007____________________________________________


_______________________________________2008____________________________________________


_______________________________________2009____________________________________________


_______________________________________2010____________________________________________


_______________________________________2011____________________________________________


...

_______________________________________2013____________________________________________


_______________________________________2014____________________________________________


_______________________________________2015____________________________________________


_______________________________________2016____________________________________________


_______________________________________2017____________________________________________


In [19]:
levels_ = list()
mappings = pd.DataFrame()
mapping_functions = dict()
for year in paths:
    episode = episodes[year]
#     agent = agents[year]

    # Load.
    actions = episode.actions_as_frame()
    states = episode.states_as_frame()
    
    # Parse.
    gaia_predictor = states[0].to_frame('GAIA Predictor')
    
#     The following line was here before
#     target_weight_russell_1000 = actions[ETF('Russell 1000')]
    target_weight_russell_1000 = actions[actions.columns[0]]
    target_weight_russell_1000.name = 'Target weight: ' + str(target_weight_russell_1000.name)
    mapping = gaia_predictor.join(target_weight_russell_1000)
    mapping_function = mapping.set_index('GAIA Predictor')

    levels_.append(episode.renderer.levels.to_frame().pct_change())
    mappings = mappings.append(mapping)
    mapping_functions[year] = mapping_function

    
#     mapping.iplot(
#         title="Hisorical GAIA predictor for Russell 1000 vs agent's target weights",
#         secondary_y='GAIA Predictor',
#         yTitle=target_weight_russell_1000.name,
#         secondary_y_title='GAIA Predictor',
#         legend={'orientation': 'h'},
#     )
#     mapping_function.iplot(
#         title='Policy: mapping from GAIA predictor (state) to target weight for Russell 1000 (action)',
#         xTitle='GAIA predictor for Russell 1000 (standardized)',
#         yTitle='Target weight for Russell 1000',
#         kind='scatter',
#         mode='markers',
#         size=4,
#     )

In [20]:
daily_ret = pd.concat(levels_).sort_index().fillna(0)
cumulative_performance = (1 + daily_ret).cumprod() - 1
cumulative_performance *= 100

aric = cumulative_performance.columns[1]
cumulative_performance['Strategy relative to Aric-Benchmark'] = cumulative_performance['Strategy'] - cumulative_performance[aric]


# Visualizations.
cumulative_performance.iplot(
    legend={'orientation': 'h'},
    yTitle='Total returns',
)

In [21]:
levels = (1 + cumulative_performance / 100)
annual_rets = (levels.resample('Y').last() / levels.resample('Y').first() - 1)

    
annual_rets['Strategy relative to Aric-Benchmark'] = annual_rets['Strategy'] - annual_rets[aric]
annual_rets.index = annual_rets.index.year
annual_rets *= 100
annual_rets.iplot(kind='bar', legend={'orientation': 'h'}, yTitle='%')

In [22]:
levels.drop('Strategy relative to Aric-Benchmark', axis='columns').tearsheet(
    benchmark=env._load_benchmark().loc['2008':].squeeze(),
    risk_free=env._load_risk_free().loc['2008':].squeeze(),
    weights=env.broker.track_record.to_frame('weights_target').iloc[1:]
)

Strategy  \
Context              From                                       2018-01-02   
                     To                                         2018-08-28   
                     Years                                        0.652055   
                     Observations                                      171   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                              0.0196092   
Return               CAGR                                        0.0186888   
                     CAGR over cash                           -0.000920358   
                     Overall return                              0.0121469   
Risk                 Volatility                                  0.0232739   
                     Downside volatility                         0.0154151   
                     Upside volatility                           0.0179229   
                     Max drawdown                               -0.0102352   
                     Martin risk                                0.00436924   
                     VaR 5%                                     -0.0025487   
                     VaR 2%                                    -0.00277667   
                     Expected shortfall 5%                     -0.00305995   
                     Expected shortfall 2%                     -0.00352835   
Risk-adjusted return Sharpe ratio                               -0.0395447   
                     Sortino ratio                              -0.0597051   
                     Calmar ratio                               -0.0899209   
                     Martin ratio                                -0.210645   
Outperformance       Benchmark name                  Index(Aric-Benchmark)   
                     CAGR over benchmark                        -0.0983079   
                     Information ratio                           -0.915744   
                     CAPM Alpha                                -0.00845542   
                     CAPM Beta                                    0.083218   
Weights              Cash(USD)                                    0.510858   
                     ETF(Russell 1000, SMART, USD)               0.0807849   
                     ETF(7-10Y T-Bills, SMART, USD)               0.408357   
                     Leverage mean                                       1   
                     Turnover daily                               0.100464   
                     Turnover annual                                25.317   

                                                     Index(Aric-Benchmark)  \
Context              From                                       2018-01-02   
                     To                                         2018-08-28   
                     Years                                        0.652055   
                     Observations                                      171   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                              0.0196092   
Return               CAGR                                         0.116997   
                     CAGR over cash                              0.0973876   
                     Overall return                              0.0748119   
Risk                 Volatility                                   0.114766   
                     Downside volatility                          0.101342   
                     Upside volatility                           0.0687842   
                     Max drawdown                               -0.0845287   
                     Martin risk                                 0.0278249   
                     VaR 5%                                     -0.0109431   
                     VaR 2%                                     -0.0159702   
                     Expected shortfall 5%                      -0.0185612   
         

In [ ]:
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
import cufflinks
cufflinks.go_offline()
init_notebook_mode(connected=False)


traces = list()
for year, series in mapping_functions.items():
    trace = go.Scatter(
        x = list(series.squeeze().index[:-1]),
        y = list(series.squeeze().values[:-1]),
        mode = 'markers',
        name = year
    )
    traces.append(trace)
    
layout = go.Layout(
    title='GAIA vs RL mapping functions',
    xaxis=dict(
        title='GAIA Mapping'
    ),
    yaxis=dict(
        title='DDPG Mapping'
        )
        
    )
fig = go.Figure(data=traces,layout=layout)
iplot(fig,filename='scatter=mode')

# iplot(traces, filename='scatter-mode')